# Ventilation Status - ML Modeling

------------
### Data Vectorization

In [3]:
from pyspark.ml import Pipeline
from pyspark.ml.feature import OneHotEncoder, OneHotEncoderEstimator, StringIndexer, VectorAssembler
from pyspark.sql.functions import *

In [4]:
dataset = spark.table("mldata_ventilation_status")
display(dataset)

Patient dataset ventilation_status City Marital Race Ethnicity Gender Suffix County State Revenue Healthcare_Coverage pct_covered age_years allergy_232347008 allergy_232350006 allergy_300913006 allergy_300916003 allergy_417532002 allergy_418689008 allergy_419263009 allergy_419474003 allergy_420174000 allergy_424213003 allergy_425525006 allergy_714035009 allergy_91930004 allergy_91934008 allergy_91935009 careplan_133899007 careplan_133901003 careplan_134435003 careplan_170836005 careplan_182964004 careplan_183401008 careplan_225358003 careplan_384758001 careplan_385691007 careplan_386257007 careplan_386522008 careplan_395082007 careplan_408869004 careplan_412776001 careplan_443402002 careplan_47387005 careplan_53950000 careplan_698360004 careplan_699728000 careplan_703040004 careplan_711282006 careplan_718347000 careplan_734163000 careplan_735984001 careplan_736252007 careplan_736254008 careplan_736285004 careplan_736353004 careplan_736690008 careplan_737434004 careplan_737471002 careplan_75162002 careplan_781831000000109 careplan_869761000000107 careplan_91251008 condition_10509002 condition_109838007 condition_110030002 condition_11218009 condition_124171000119105 condition_126906006 condition_127013003 condition_127295002 condition_128613002 condition_1501000119109 condition_1551000119108 condition_156073000 condition_157141000119108 condition_15724005 condition_15777000 condition_16114001 condition_161621004 condition_161622006 condition_162573006 condition_162864005 condition_1734006 condition_185086009 condition_190905008 condition_19169002 condition_192127007 condition_195662009 condition_195967001 condition_196416002 condition_197927001 condition_198992004 condition_200936003 condition_201834006 condition_206523001 condition_22298006 condition_225444004 condition_230265002 condition_230690007 condition_232353008 condition_233604007 condition_233678006 condition_235919008 condition_236077008 condition_237602007 condition_239720000 condition_239872002 condition_239873007 condition_24079001 condition_241929008 condition_254632001 condition_254637007 condition_254837009 condition_262574004 condition_263102004 condition_26929004 condition_271737000 condition_275272006 condition_283371005 condition_283385000 condition_284549007 condition_284551006 condition_287185009 condition_301011002 condition_302870006 condition_307731004 condition_30832001 condition_314994000 condition_33737001 condition_359817006 condition_35999006 condition_363406005 condition_367498001 condition_368581000119106 condition_36923009 condition_36971009 condition_370143000 condition_370247008 condition_38822007 condition_398254007 condition_39848009 condition_399211009 condition_40055000 condition_40275004 condition_403190006 condition_403191005 condition_403192003 condition_406602003 condition_408512008 condition_410429000 condition_422034002 condition_424132000 condition_425048006 condition_427089005 condition_428251008 condition_429007001 condition_429280009 condition_431855005 condition_431856006 condition_433144002 condition_43878008 condition_44054006 condition_443165006 condition_444448004 condition_444470001 condition_44465007 condition_444814009 condition_446096008 condition_448417001 condition_448813005 condition_449868002 condition_45816000 condition_47200007 condition_47505003 condition_47693006 condition_48333001 condition_49436004 condition_53741008 condition_55680006 condition_55822004 condition_5602001 condition_58150001 condition_59621000 condition_6072007 condition_60951000119105 condition_62106007 condition_62564004 condition_64859006 condition_65275009 condition_65363002 condition_65710008 condition_65966004 condition_67811000119102 condition_68496003 condition_698423002 condition_698754002 condition_69896004 condition_703151001 condition_70704007 condition_707577004 condition_713197008 condition_7200002 condition_72892002 condition_74400008 condition_75498004 condition_79586000 condition_80394007 condition_82423001 condition_83664006 c

In [5]:
label = "ventilation_status"
allColumns = dataset.columns

categoricalColumns = [
  "City",
  "Marital",
  "Race",
  "Ethnicity",
  "Gender",
  "Suffix",
  "County",
#   "State",
  "smoker_status"
]

# numericalColumns = ["num1",
#                     "num2"]

ignoreColumns = ["Patient", "dataset", "State", label]

numericalColumns = list(set(allColumns) - set(categoricalColumns) - set(ignoreColumns))
# print(numericalColumns)

categoricalColumnsclassVec = [c + "classVec" for c in categoricalColumns]

stages = []

In [6]:
for categoricalColumn in categoricalColumns:
  print(categoricalColumn)
  ## Category Indexing with StringIndexer
  stringIndexer = StringIndexer(inputCol=categoricalColumn, outputCol = categoricalColumn+"Index").setHandleInvalid("skip")
  ## Use OneHotEncoder to convert categorical variables into binary SparseVectors
  encoder = OneHotEncoder(inputCol=categoricalColumn+"Index", outputCol=categoricalColumn+"classVec")
  ## Add stages
  stages += [stringIndexer, encoder]

City
Marital
Race
Ethnicity
Gender
Suffix
County
smoker_status

In [7]:
## Convert label into label indices using the StringIndexer
label_stringIndexer = StringIndexer(inputCol = label, outputCol = "label", stringOrderType="alphabetAsc").setHandleInvalid("keep")
stages += [label_stringIndexer]

In [8]:
assemblerInputs = categoricalColumnsclassVec + numericalColumns
assembler = VectorAssembler(inputCols = assemblerInputs, outputCol="features").setHandleInvalid("skip")
stages += [assembler]

In [9]:
prepPipeline = Pipeline().setStages(stages)
# pipelineModel = prepPipeline.fit(train)
pipelineModel = prepPipeline.fit(dataset)
dataset = pipelineModel.transform(dataset)

# train = pipelineModel.transform(train)
# test = pipelineModel.transform(test)

In [10]:
train = dataset.filter(col("dataset") == "train")
train = train.filter(col("ventilation_status").isNotNull()).sample(False, .20, 1337)

test = dataset.filter(col("dataset") == "test")

In [11]:
display(train.select("Patient", "ventilation_status", "label", "features"))

Patient ventilation_status label features 0170e255-75fa-4160-8d8d-4d3a3b7dbaa9 0 0.0 List(0, 1193, List(17, 356, 358, 366, 376, 423, 453, 468, 498, 505, 512, 521, 526, 545, 550, 556, 563, 564, 571, 576, 579, 595, 597, 601, 627, 637, 639, 651, 655, 681, 694, 714, 761, 765, 809, 810, 815, 838, 875, 877, 887, 888, 890, 913, 922, 934, 937, 959, 962, 965, 971, 975, 982, 1040, 1045, 1059, 1074, 1091, 1104, 1135, 1155, 1173, 1176, 1180), List(1.0, 1.0, 1.0, 1.0, 1.0, 0.0063059923990430545, 0.09, 18.0, 0.31, 0.028911420717952063, 0.06, 0.07557340278415407, 0.10276546089803718, 1.0, 0.11723124987022318, 0.0489374465669969, 0.14, 567845.15, 0.001, 1.0, 0.8998225485476999, 0.06166532242398385, 0.06166532242398385, 1.0, 1.0, 0.08, 1.0, 0.10276546089803718, 0.028911420717952063, 0.9081826122546464, 0.04, 0.14, 1.0, 0.16, 0.09181738774535364, 0.0231908213775118, 0.06166532242398385, 0.09, 1.0, 1.0, 18.0, 0.07225938085966968, 0.00491591765818551, 2.0, 4032.0, 18.0, 24.0, 1.0, 0.11723124987022318, 0.07, 0.028911420717952063, 1.0, 0.07557340278415407, 2791.48, 0.13, 0.02, 1.0, 0.17, 1.0, 1.0, 0.07557340278415407, 21.21013004791239, 0.06166532242398385, 0.43)) 07b68c06-830d-442f-9718-0564053cbcd2 0 0.0 List(0, 1193, List(7, 350, 352, 356, 357, 358, 366, 376, 423, 453, 468, 498, 505, 512, 521, 526, 545, 550, 556, 563, 564, 571, 579, 595, 597, 601, 627, 637, 639, 651, 655, 681, 694, 714, 761, 765, 809, 810, 815, 838, 875, 887, 888, 890, 922, 934, 937, 962, 965, 971, 975, 982, 1040, 1045, 1074, 1091, 1104, 1155, 1173, 1176, 1180), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.0063059923990430545, 0.12, 31.0, 0.34, 0.028911420717952063, 0.1, 0.07557340278415407, 0.10276546089803718, 8.0, 0.11723124987022318, 0.0489374465669969, 0.08, 898326.72, 0.001, 0.8998225485476999, 0.06166532242398385, 0.06166532242398385, 1.0, 1.0, 0.07, 8.0, 0.10276546089803718, 0.028911420717952063, 0.9081826122546464, 0.02, 0.14, 1.0, 0.2, 0.09181738774535364, 0.0231908213775118, 0.06166532242398385, 0.14, 1.0, 31.0, 0.07225938085966968, 0.004291489849038444, 6742.0, 31.0, 270.0, 0.11723124987022318, 0.1, 0.028911420717952063, 1.0, 0.07557340278415407, 3855.16, 0.09, 1.0, 0.15, 8.0, 0.07557340278415407, 41.4072553045859, 0.06166532242398385, 0.37)) 150b09f2-1604-4fc6-92fe-62c5bf85bb02 0 0.0 List(0, 1193, List(10, 351, 352, 357, 358, 364, 374, 379, 382, 384, 399, 404, 417, 423, 440, 449, 453, 468, 470, 498, 499, 502, 505, 512, 513, 517, 519, 520, 521, 522, 526, 545, 550, 552, 556, 563, 564, 571, 579, 595, 597, 603, 637, 639, 651, 653, 655, 663, 665, 681, 689, 694, 714, 719, 721, 727, 731, 733, 746, 765, 766, 767, 770, 773, 779, 780, 783, 788, 791, 794, 796, 800, 809, 810, 815, 822, 824, 826, 831, 835, 836, 838, 849, 853, 870, 887, 888, 890, 895, 905, 911, 915, 922, 931, 934, 962, 964, 965, 971, 977, 982, 990, 997, 1031, 1037, 1040, 1043, 1045, 1049, 1050, 1051, 1053, 1056, 1059, 1067, 1071, 1084, 1088, 1091, 1095, 1100, 1101, 1104, 1125, 1140, 1141, 1155, 1158, 1161, 1173, 1174, 1176, 1180), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 73.0, 4.0, 87.0, 529.0, 35.0, 154.0, 0.008499529020943426, 108.0, 5.0, 0.13, 40.0, 1.0, 0.32, 5.0, 538.0, 0.02910802721501823, 0.12, 61.0, 1.0, 1.0, 61.0, 0.07534587460797187, 58.0, 0.10272853949013742, 22.0, 0.11683572928809713, 8.0, 0.06523607583600394, 0.06, 210116.87, 0.001, 0.8613066543993052, 0.061904850057733475, 0.061904850057733475, 1.0, 0.05, 22.0, 0.10272853949013742, 1.0, 0.02910802721501823, 1.0, 126.0, 0.9035674362671776, 1.0, 0.02, 0.13, 5.0, 10.0, 4.0, 31.0, 58.0, 154.0, 0.26, 157.0, 73.0, 73.0, 87.0, 1.0, 99.0, 157.0, 1.0, 3.0, 58.0, 138.0, 21.0, 0.09643256373282227, 0.039206590356462206, 0.061904850057733475, 1.0, 35.0, 8.0, 87.0, 1.0, 126.0, 0.15, 8.0, 3.0, 31.0, 40.0, 0.19244165593916832, 0.2463299115392305, 5.0, 108.0, 154.0, 31.0, 5054.0, 1.0, 40.0, 0.11683572928809713, 99.0, 0.1, 0.02910802721501823, 1.0, 0.07534587460797187, 1.0, 108.0, 138.0, 1.0, 51758.06999999999, 5.0, 0.1, 3.0, 1.0, 61.0, 4.0, 126.0, 0.01, 138.0, 10.0

In [12]:
print("Number of rows in `train`: " + str(train.count()) + "\nNumber of rows in `test`: " + str(test.count()))

Number of rows in `train`: 14677
Number of rows in `test`: 29474

In [13]:
pipelineModel.write().overwrite().save("/mnt/data/ml/ventilationstatus/pipeline")
# display(dbutils.fs.ls("/mnt/data/ml/ventilationstatus/pipeline"))

### Logistic Regression

In [15]:
from pyspark.ml.classification import LogisticRegression
from pyspark.ml.tuning import ParamGridBuilder, CrossValidator
from pyspark.ml.evaluation import BinaryClassificationEvaluator
from pyspark.mllib.evaluation import BinaryClassificationMetrics

In [16]:
lr = LogisticRegression(labelCol="ventilation_status", featuresCol="features")
# lr.fit(train)

In [17]:
lrparamGrid = (ParamGridBuilder()
             .addGrid(lr.regParam, [0.01, 0.1, 0.25])
             .addGrid(lr.elasticNetParam, [0.0, 0.1, 0.25])
             .addGrid(lr.maxIter, [1, 5, 10])
             .build())

In [18]:
lrevaluator = BinaryClassificationEvaluator(rawPredictionCol="rawPrediction", metricName = "areaUnderPR")

In [19]:
# Create 5-fold CrossValidator
lrcv = CrossValidator(estimator = lr,
                      estimatorParamMaps = lrparamGrid,
                      evaluator = lrevaluator,
                      numFolds = 3)

In [20]:
lrcvModel = lrcv.fit(train)

lrcvModel.write().overwrite().save("/mnt/data/ml/ventilationstatus/lr")

print(lrcvModel)

MLlib will automatically track trials in MLflow. After your tuning fit() call has completed, view the MLflow UI to see logged runs.
CrossValidatorModel_8856b5bff71c

In [21]:
lrpredictions = lrcvModel.transform(train)
lrpredictions_test = lrcvModel.transform(test)
# display(lrpredictions)

In [22]:
print('Accuracy:', lrevaluator.evaluate(lrpredictions))
print('AUC:', BinaryClassificationMetrics(lrpredictions['label','prediction'].rdd).areaUnderROC)
print('PR:', BinaryClassificationMetrics(lrpredictions['label','prediction'].rdd).areaUnderPR)

Accuracy: 0.16361477591968326
AUC: 0.6143996416643134
PR: 0.0017064212425714606

### Decision Tree

In [24]:
from pyspark.ml.classification import DecisionTreeClassifier
from pyspark.ml.tuning import ParamGridBuilder, CrossValidator
from pyspark.ml.evaluation import BinaryClassificationEvaluator

In [25]:
dt = DecisionTreeClassifier(labelCol="label", featuresCol="features")

In [26]:
dtparamGrid = (ParamGridBuilder()
             .addGrid(dt.maxDepth, [2, 5, 10, 25])
             .addGrid(dt.maxBins, [10, 20, 50])
             .build())

In [27]:
dtevaluator = BinaryClassificationEvaluator(rawPredictionCol="rawPrediction")

In [28]:
# Create 5-fold CrossValidator
dtcv = CrossValidator(estimator = dt,
                      estimatorParamMaps = dtparamGrid,
                      evaluator = dtevaluator,
                      numFolds = 3)

In [29]:
dtcvModel = dtcv.fit(train)

dtcvModel.write().overwrite().save("/mnt/data/ml/ventilationstatus/dt")

print(dtcvModel)

MLlib will automatically track trials in MLflow. After your tuning fit() call has completed, view the MLflow UI to see logged runs.
CrossValidatorModel_5e3f4ad5b816

In [30]:
dtpredictions = dtcvModel.transform(train)
dtpredictions_test = dtcvModel.transform(test)

# display(dtpredictions)

In [31]:
print('Accuracy:', dtevaluator.evaluate(dtpredictions))
print('AUC:', BinaryClassificationMetrics(dtpredictions['label','prediction'].rdd).areaUnderROC)
print('PR:', BinaryClassificationMetrics(dtpredictions['label','prediction'].rdd).areaUnderPR)

Accuracy: 0.6787073473749161
AUC: 0.9171418578836125
PR: 0.06216925159410167

### Random Forest

In [33]:
from pyspark.ml.classification import RandomForestClassifier
from pyspark.ml.tuning import ParamGridBuilder, CrossValidator
from pyspark.ml.evaluation import BinaryClassificationEvaluator

In [34]:
rf = RandomForestClassifier(labelCol="label", featuresCol="features")

In [35]:
rfparamGrid = (ParamGridBuilder()
               .addGrid(rf.maxDepth, [2, 5, 10])
               .addGrid(rf.maxBins, [5, 10, 20])
               .addGrid(rf.numTrees, [5, 20, 50])
             .build())

In [36]:
rfevaluator = BinaryClassificationEvaluator(rawPredictionCol="rawPrediction")

In [37]:
# Create 5-fold CrossValidator
rfcv = CrossValidator(estimator = rf,
                      estimatorParamMaps = rfparamGrid,
                      evaluator = rfevaluator,
                      numFolds = 3)

In [38]:
rfcvModel = rfcv.fit(train)

rfcvModel.write().overwrite().save("/mnt/data/ml/ventilationstatus/rf")

# print(rfcvModel)

MLlib will automatically track trials in MLflow. After your tuning fit() call has completed, view the MLflow UI to see logged runs.

In [39]:
rfpredictions = rfcvModel.transform(train)
rfpredictions_test = rfcvModel.transform(test)

# display(rfpredictions)

In [40]:
print('Accuracy:', rfevaluator.evaluate(rfpredictions))
print('AUC:', BinaryClassificationMetrics(rfpredictions['label','prediction'].rdd).areaUnderROC)
print('PR:', BinaryClassificationMetrics(rfpredictions['label','prediction'].rdd).areaUnderPR)

Accuracy: 0.802141396438145
AUC: 0.8049459287531806
PR: 0.0040506062736685115

In [41]:
display(dbutils.fs.ls("/mnt/data/ml/ventilationstatus/"))

path name size dbfs:/mnt/data/ml/ventilationstatus/dt/ dt/ 0 dbfs:/mnt/data/ml/ventilationstatus/lr/ lr/ 0 dbfs:/mnt/data/ml/ventilationstatus/pipeline/ pipeline/ 0 dbfs:/mnt/data/ml/ventilationstatus/rf/ rf/ 0

In [42]:
import pandas as pd

def ExtractFeatureImportance(featureImp, dataset, featuresCol):
    list_extract = []
    for i in dataset.schema[featuresCol].metadata["ml_attr"]["attrs"]:
        list_extract = list_extract + dataset.schema[featuresCol].metadata["ml_attr"]["attrs"][i]
    varlist = pd.DataFrame(list_extract)
    varlist['score'] = varlist['idx'].apply(lambda x: featureImp[x])
    return(varlist.sort_values('score', ascending = False))
  
  
# ExtractFeatureImportance(model.stages[-1].featureImportances, dataset, "features")
dataset_fi = ExtractFeatureImportance(dtcvModel.bestModel.featureImportances, train, "features")
dataset_fi = sqlContext.createDataFrame(dataset_fi)
display(dataset_fi)

idx name score 1173 age_years 0.48622925258203065 460 procedure_703423002 0.13804657172461782 533 procedure_265764009 0.06593753516512511 1084 18262-6_Max 0.04079259289504452 1060 9279-1_Max 0.0345049971595868 456 condition_431856006 0.0310117096168183 822 careplan_443402002 0.022965355850233928 505 City_Age_25_29 0.02248011154408746 1091 City_Income_50_75K 0.021798896042751478 266 CityclassVec_Cheshire 0.021568562248191207 1179 condition_19169002 0.021227518399757637 406 medication_2001499 0.018951600321388956 305 CityclassVec_Chesterfield 0.016397365393833185 659 procedure_15081005 0.012499470873400744 525 medication_308971 0.012496032229407063 259 CityclassVec_Paxton 0.012260901426458738 239 CityclassVec_Oak Bluffs 0.01224408263163684 350 MaritalclassVec_M 0.00858744389562937 1169 medication_752899 0.0 1170 procedure_384692006 0.0 1171 condition_237602007 0.0 1172 procedure_165829005 0.0 1168 condition_40275004 0.0 1175 careplan_737471002 0.0 1167 immunization_52 0.0 1174 allergy_91935009 0.0 1166 medication_583214 0.0 377 condition_192127007 0.0 1178 careplan_133899007 0.0 1176 City_Age_45_49 0.0 1186 procedure_51116004 0.0 1192 condition_33737001 0.0 1191 medication_1946840 0.0 1190 condition_62564004 0.0 1189 medication_259255 0.0 1188 785-6_Min 0.0 1187 careplan_170836005 0.0 1185 medication_1665227 0.0 1177 medication_834061 0.0 1184 procedure_699253003 0.0 1183 condition_6072007 0.0 1182 medication_311700 0.0 1181 8302-2_Max 0.0 1180 City_Education_HS_Degree 0.0 1164 2160-0_Min 0.0 1165 careplan_134435003 0.0 1160 condition_262574004 0.0 1163 careplan_75162002 0.0 1136 procedure_271442007 0.0 1142 DALY_StdDev 0.0 1141 condition_271737000 0.0 1140 20565-8_Min 0.0 1139 medication_807283 0.0 1138 allergy_300913006 0.0 1137 medication_1605257 0.0 1135 careplan_736254008 0.0 1144 City_Age_0_4 0.0 1134 condition_427089005 0.0 1133 39156-5_Min 0.0 1132 condition_410429000 0.0 1131 condition_236077008 0.0 1130 medication_746030 0.0 1129 procedure_275833003 0.0 1143 medication_197319 0.0 1145 City_Age_5_9 0.0 1162 procedure_45595009 0.0 1154 procedure_252160004 0.0 1161 2093-3_Avg 0.0 1159 3094-0_Avg 0.0 1158 condition_59621000 0.0 1157 procedure_23426006 0.0 1156 procedure_29303009 0.0 1155 City_Age_80_84 0.0 1153 2069-3_StdDev 0.0 1146 procedure_90470006 0.0 1152 medication_856980 0.0 1151 condition_195662009 0.0 1150 medication_978950 0.0 1149 medication_1791701 0.0 1148 condition_254632001 0.0 1147 procedure_714812005 0.0 0 CityclassVec_Boston 0.0 3 CityclassVec_Cambridge 0.0 1 CityclassVec_Worcester 0.0 50 CityclassVec_Wellesley 0.0 57 CityclassVec_Watertown 0.0 56 CityclassVec_North Andover 0.0 55 CityclassVec_Milford 0.0 54 CityclassVec_Franklin 0.0 53 CityclassVec_Randolph 0.0 52 CityclassVec_Lexington 0.0 51 CityclassVec_Falmouth 0.0 49 CityclassVec_Dartmouth 0.0 40 CityclassVec_Holyoke 0.0 48 CityclassVec_Braintree 0.0 47 CityclassVec_Shrewsbury 0.0 46 CityclassVec_Chelmsford 0.0 45 CityclassVec_Dracut 0.0 44 CityclassVec_Andover 0.0 43 CityclassVec_Stoughton 0.0 42 CityclassVec_Natick 0.0 58 CityclassVec_Milton 0.0 59 CityclassVec_Tewksbury 0.0 60 CityclassVec_Agawam 0.0 61 CityclassVec_Gloucester 0.0 76 CityclassVec_Walpole 0.0 75 CityclassVec_Belmont 0.0 74 CityclassVec_Danvers 0.0 73 CityclassVec_Mansfield 0.0 72 CityclassVec_West Springfield 0.0 71 CityclassVec_Northampton 0.0 70 CityclassVec_Middleborough 0.0 69 CityclassVec_Dedham 0.0 68 CityclassVec_Wakefield 0.0 67 CityclassVec_Melrose 0.0 66 CityclassVec_Norwood 0.0 65 CityclassVec_North Attleborough 0.0 64 CityclassVec_Needham 0.0 63 CityclassVec_Burlington 0.0 62 CityclassVec_Saugus 0.0 41 CityclassVec_Beverly 0.0 39 CityclassVec_Amherst 0.0 2 CityclassVec_Springfield 0.0 11 CityclassVec_Fall River 0.0 18 CityclassVec_Chicopee 0.0 17 CityclassVec_Taunton 0.0 16 CityclassVec_Waltham 0.0 15 CityclassVec_Malden 0.0 14 CityclassVec_Haverhill 0.0 13 CityclassVec_Framingham 0.0 12 CityclassVec_Somerville 0.0 10 CityclassVec_Lawrence 0.0 38 CityclassVec_Westfiel